# HW1 布尔查询之BSBI与索引压缩

本次作业使用斯坦福大学[CS 276 / LING 286: Information Retrieval and Web Search](https://web.stanford.edu/class/cs276/)课程的代码框架来实现。具体来说主要包含的内容有：
1. [索引构建 (40%)](#索引构建与检索-(40%)) 使用BSBI方法模拟在内存不足的情况下的索引构建方式，并应用于布尔查询
2. [索引压缩 (30%)](#索引压缩-(30%)) 使用可变长编码对构建的索引进行压缩
3. [布尔检索 (10%)](#布尔联合检索-(10%)) 对空格分隔的单词查询进行联合（与）布尔检索
3. [实验报告 (10%)](#Report-(25%)) 描述你的代码并回答一些问题
4. [额外的编码方式 (10%)](#额外的编码方式-(10%)) 鼓励使用额外的编码方式对索引进行压缩 (例如, gamma-encoding)

In [72]:
# You can add additional imports here
import sys
import pickle as pkl
import array
import os
import timeit
import contextlib
# my import
from bitstring import BitArray


# 数据集

实验使用的文本数据是stanford.edu域下的网页内容，可从http://web.stanford.edu/class/cs276/pa/pa1-data.zip 下载。以下代码将大约170MB的文本数据下载到当前目录下，

In [73]:
import urllib.request
import zipfile

# data_url = "http://web.stanford.edu/class/cs276/pa/pa1-data.zip"
# data_dir = "pa1-data"
# # urllib.request.urlretrieve(data_url, data_dir + ".zip")
# zip_ref = zipfile.ZipFile(data_dir + ".zip", "r")
# zip_ref.extractall()
# zip_ref.close()

之后构建的索引会被存储到`output_dir`，`tmp`会存储测试数据（toy-data）所生成的一些临时文件

In [74]:
try:
    os.mkdir("output_dir")
except FileExistsError:
    pass
try:
    os.mkdir("tmp")
except FileExistsError:
    pass
try:
    os.mkdir("toy_output_dir")
except FileExistsError:
    pass

在数据目录下有10个子目录（命名0-9）

In [75]:
sorted(os.listdir("pa1-data"))

['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']

每一个子目录下的文件都包含一个独立网页的内容。可以认为在同一子目录下没有同名文件，即每个文件的绝对路径不会相同。

In [76]:
sorted(os.listdir("pa1-data/0"))[:10]

['3dradiology.stanford.edu_',
 '3dradiology.stanford.edu_patient_care_Case%2520studies_AVM.html',
 '3dradiology.stanford.edu_patient_care_case_studies.html',
 '5-sure.stanford.edu_',
 '50years.stanford.edu_',
 'a3cservices.stanford.edu_awards_nominate_',
 'a3cservices.stanford.edu_facilities_',
 'a3cservices.stanford.edu_lead_',
 'aa.stanford.edu_',
 'aa.stanford.edu_about_aviation.php']

所有的网页内容已经经过处理，仅包含由空格分隔开的单词，不再需要进行额外的标准化工作。

In [77]:
with open("pa1-data/0/3dradiology.stanford.edu_", "r") as f:
    print(f.read())

3d radiology lab stanford university school of medicine stanford school of medicine 3d and quantitative imaging in the department of radiology search this site only stanford medical sites ways to give find a person alumni lane library ways to give find a person about us mission to develop and apply innovative techniques for efficient quantitative analysis and display of medical imaging data through interdisciplinary collaboration goals education to train physicians and technologists locally and worldwide in the latest developments in 3d and quantitative imaging research to develop new approaches to the exploration analysis and quantitative assesment of diagnostic images that result in a new and or more cost effective diagnostic approaches and b new techniques for the design and planning and monitoring of therapy patient care to deliver valid clinically relevant visualization and analysis of medical imaging data to the stanford community locations richard m lucas magnetic resonance imag

# 索引构建与检索 (40%)

作业的第一部分是使用**blocked sort-based indexing (BSBI)** 算法来构建倒排索引并实现布尔检索。关于BSBI算法可以参考老师课件或者斯坦福教材[Section 4.2](http://nlp.stanford.edu/IR-book/pdf/04const.pdf)。以下摘自教材内容

> To construct an index, we first make a pass through the collection assembling all term-docID pairs. We then sort the pairs with the term as the dominant key and docID as the secondary key. Finally, we organize the docIDs for each term into a postings list and compute statistics like term and document frequency. For small collections, all this can be done in memory. 

对于无法在内存一次性处理的较大数据集，将会使用到二级存储（如：磁盘）。

## IdMap (6%)

再次引用教材 Section 4.2:

> To make index construction more efficient, we represent terms as termIDs (instead of strings), where each termID is a unique serial number. We can build the mapping from terms to termIDs on the fly while we are processing the collection. Similarly, we also represent documents as docIDs (instead of strings).

我们首先定义一个辅助类`IdMap`，用于将字符串和数字ID进行相互映射，以满足我们在term和termID、doc和docID间转换的需求。

实现以下代码中的`_get_str` 和 `_get_id`函数，IdMap类的唯一接口是`__getitem__`，它是一个特殊函数，重写了下标运算`[]`,根据下标运算键的类型得到正确的映射值（如果不存在需要添加）。（特殊函数可参考[官方文档](https://docs.python.org/3.7/reference/datamodel.html#special-method-names)）
<br>
<br>
我们会用到字典来将字符串转换为数字，用列表来将数字转换为字符串。(4%)

In [78]:
class IdMap:
    """Helper class to store a mapping from strings to ids."""

    def __init__(self):
        self.str_to_id = {}
        self.id_to_str = []

    def __len__(self):
        """Return number of terms stored in the IdMap"""
        
        return len(self.id_to_str)

    def _get_str(self, i):
        """Returns the string corresponding to a given id (`i`)."""
        ### Begin your code
        return self.id_to_str[i]
        ### End your code

    def _get_id(self, s):
        """Returns the id corresponding to a string (`s`).
        If `s` is not in the IdMap yet, then assigns a new id and returns the new id.
        """
        ### Begin your code
        if s not in self.str_to_id:
            self.id_to_str.append(s)
            self.str_to_id[s] = len(self.id_to_str) - 1
        return self.str_to_id[s]
        ### End your code

    def __getitem__(self, key):
        """If `key` is a integer, use _get_str;
        If `key` is a string, use _get_id;"""
        if type(key) is int:
            return self._get_str(key)
        elif type(key) is str:
            return self._get_id(key)
        else:
            raise TypeError

确保代码能通过以下简单测试样例 (2%)

In [79]:
testIdMap = IdMap()

assert testIdMap["a"] == 0, "Unable to add a new string to the IdMap"
assert testIdMap["bcd"] == 1, "Unable to add a new string to the IdMap"
assert testIdMap["a"] == 0, "Unable to retrieve the id of an existing string"
assert (
    testIdMap[1] == "bcd"
), "Unable to retrive the string corresponding to a\
                                given id"
try:
    testIdMap[2]
except IndexError as e:
    assert True, "Doesn't throw an IndexError for out of range numeric ids"
assert len(testIdMap) == 2

之后会需要你自己来写测试样例来确保你的程序正常运行

## 将倒排列表编码成字节数组 (2%)

为了高效地从磁盘读写倒排列表（文档ID），我们将其存储为字节数组的形式。代码提供了`UncompressedPostings`类来用静态函数实现对倒排列表的编码和解码。在之后的任务中你需要使用该接口实现索引压缩版本（可变长编码）。

参考:
1. https://docs.python.org/3/library/array.html
2. https://pymotw.com/3/array/#module-array

In [80]:
class UncompressedPostings:

    @staticmethod
    def encode(postings_list):
        """Encodes postings_list into a stream of bytes

        Parameters
        ----------
        postings_list: List[int]
            List of docIDs (postings)

        Returns
        -------
        bytes
            bytearray representing integers in the postings_list
        """
        return array.array("L", postings_list).tobytes()

    @staticmethod
    def decode(encoded_postings_list):
        """Decodes postings_list from a stream of bytes

        Parameters
        ----------
        encoded_postings_list: bytes
            bytearray representing encoded postings list as output by encode
            function

        Returns
        -------
        List[int]
            Decoded list of docIDs from encoded_postings_list
        """

        decoded_postings_list = array.array("L")
        decoded_postings_list.frombytes(encoded_postings_list)
        return decoded_postings_list.tolist()

运行以下代码查看其工作方式 (2%)

In [81]:
x = UncompressedPostings.encode([1, 2, 3])
print(x)
print(UncompressedPostings.decode(x))

b'\x01\x00\x00\x00\x02\x00\x00\x00\x03\x00\x00\x00'
[1, 2, 3]


## 磁盘上的倒排索引 (2%)

> With main memory insufficient, we need to use an external sorting algorithm, that is, one that uses disk. For acceptable speed, the central requirement of such an algorithm is that it minimize the number of random disk seeks during sorting - sequential disk reads are far faster than seeks. 

在这一部分我们提供了一个基类`InvertedIndex`，之后会在此基础上构建它的子类`InvertedIndexWriter`, `InvertedIndexIterator` 和 `InvertedIndexMapper`。在Python中我们常用`cPickle`进行序列化，但是它并不支持部分读和部分写，无法满足BSBI算法的需要，所以我们需要定义自己的存储方式。

In [82]:
class InvertedIndex:
    """A class that implements efficient reads and writes of an inverted index
    to disk

    Attributes
    ----------
    postings_dict: Dictionary mapping: termID->(start_position_in_index_file,
                                                number_of_postings_in_list,
                                               length_in_bytes_of_postings_list)
        This is a dictionary that maps from termIDs to a 3-tuple of metadata
        that is helpful in reading and writing the postings in the index file
        to/from disk. This mapping is supposed to be kept in memory.
        start_position_in_index_file is the position (in bytes) of the postings
        list in the index file
        number_of_postings_in_list is the number of postings (docIDs) in the
        postings list
        length_in_bytes_of_postings_list is the length of the byte
        encoding of the postings list

    terms: List[int]
        A list of termIDs to remember the order in which terms and their
        postings lists were added to index.

        After Python 3.7 we technically no longer need it because a Python dict
        is an OrderedDict, but since it is a relatively new feature, we still
        maintain backward compatibility with a list to keep track of order of
        insertion.
    """

    def __init__(self, index_name, postings_encoding=None, directory=""):
        """
        Parameters
        ----------
        index_name (str): Name used to store files related to the index
        postings_encoding: A class implementing static methods for encoding and
            decoding lists of integers. Default is None, which gets replaced
            with UncompressedPostings
        directory (str): Directory where the index files will be stored
        """

        self.index_file_path = os.path.join(directory, index_name + ".index")
        self.metadata_file_path = os.path.join(directory, index_name + ".dict")

        if postings_encoding is None:
            self.postings_encoding = UncompressedPostings
        else:
            self.postings_encoding = postings_encoding
        self.directory = directory

        self.postings_dict = {}
        self.terms = []  # Need to keep track of the order in which the
        # terms were inserted. Would be unnecessary
        # from Python 3.7 onwards

    def __enter__(self):
        """Opens the index_file and loads metadata upon entering the context"""
        # Open the index file
        self.index_file = open(self.index_file_path, "rb+")

        # Load the postings dict and terms from the metadata file
        with open(self.metadata_file_path, "rb") as f:
            self.postings_dict, self.terms = pkl.load(f)
            self.term_iter = self.terms.__iter__()

        return self

    def __exit__(self, exception_type, exception_value, traceback):
        """Closes the index_file and saves metadata upon exiting the context"""
        # Close the index file
        self.index_file.close()

        # Write the postings dict and terms to the metadata file
        with open(self.metadata_file_path, "wb") as f:
            pkl.dump([self.postings_dict, self.terms], f)

因为是在与磁盘上的文件进行交互，所以我们提供了`__enter__`和`__exit__`函数，它使得我们能够像使用python中文件IO一样使用`with`语句。（参考[上下文管理器官方文档](https://docs.python.org/3/library/contextlib.html)）

以下是使用 `InvertedIndexWriter` 上下文管理器的实例: (2%)

```python
with InvertedIndexWriter('test', directory='tmp/') as index:
    # Some code here
```

## 索引 (30%)

> BSBI (i) segments the collection into parts of equal size, (ii) sorts the termID-docID pairs of each part in memory, (iii) stores intermediate sorted results on disk, and (iv) merges all intermediate results into the final index. 

你需要将每一个子目录当做一个块（block），并且在构建索引的过程中每次只能加载一个块（模拟内存不足）。注意到我们是将操作系统意义上的块进行了抽象。你可以认为每个块足够小，能被装载进内存。

在这一部分，我们将阶段性地构造类`BSBIIndex`。函数`index`给出了BSBI算法的框架，而你的工作则是在接下来的部分中实现函数`parse_block`, `invert_write` 和 `merge`。

In [83]:
# Do not make any changes here, they will be overwritten while grading
class BSBIIndex:
    """
    Attributes
    ----------
    term_id_map(IdMap): For mapping terms to termIDs
    doc_id_map(IdMap): For mapping relative paths of documents (eg
        0/3dradiology.stanford.edu_) to docIDs
    data_dir(str): Path to data
    output_dir(str): Path to output index files
    index_name(str): Name assigned to index
    postings_encoding: Encoding used for storing the postings.
        The default (None) implies UncompressedPostings
    """

    def __init__(self, data_dir, output_dir, index_name="BSBI", postings_encoding=None):
        self.term_id_map = IdMap()
        self.doc_id_map = IdMap()
        self.data_dir = data_dir
        self.output_dir = output_dir
        self.index_name = index_name
        self.postings_encoding = postings_encoding

        # Stores names of intermediate indices
        self.intermediate_indices = []

    def save(self):
        """Dumps doc_id_map and term_id_map into output directory"""

        with open(os.path.join(self.output_dir, "terms.dict"), "wb") as f:
            pkl.dump(self.term_id_map, f)
        with open(os.path.join(self.output_dir, "docs.dict"), "wb") as f:
            pkl.dump(self.doc_id_map, f)

    def load(self):
        """Loads doc_id_map and term_id_map from output directory"""

        with open(os.path.join(self.output_dir, "terms.dict"), "rb") as f:
            self.term_id_map = pkl.load(f)
        with open(os.path.join(self.output_dir, "docs.dict"), "rb") as f:
            self.doc_id_map = pkl.load(f)

    def index(self):
        """Base indexing code

        This function loops through the data directories,
        calls parse_block to parse the documents
        calls invert_write, which inverts each block and writes to a new index
        then saves the id maps and calls merge on the intermediate indices
        """
        for block_dir_relative in sorted(next(os.walk(self.data_dir))[1]):
            td_pairs = self.parse_block(block_dir_relative)
            index_id = "index_" + block_dir_relative
            self.intermediate_indices.append(index_id)
            with InvertedIndexWriter(
                index_id,
                directory=self.output_dir,
                postings_encoding=self.postings_encoding,
            ) as index:
                self.invert_write(td_pairs, index)
                td_pairs = None
        self.save()
        with InvertedIndexWriter(
            self.index_name,
            directory=self.output_dir,
            postings_encoding=self.postings_encoding,
        ) as merged_index:
            with contextlib.ExitStack() as stack:
                indices = [
                    stack.enter_context(
                        InvertedIndexIterator(
                            index_id,
                            directory=self.output_dir,
                            postings_encoding=self.postings_encoding,
                        )
                    )
                    for index_id in self.intermediate_indices
                ]
                self.merge(indices, merged_index)

### 解析 (10%)

> The function `parse_block`  parses documents into termID-docID pairs and accumulates the pairs in memory until a block of a fixed size is full. We choose the block size to fit comfortably into memory to permit a fast in-memory sort. 

你需要将每一个子目录当做一个块，`parse_block`接收子目录路径作为参数。同一子目录下所有文件名都是不同的。 (5%)

_注意 - 我们使用 `BSBIIndex` 继承 `BSBIIndex`, 这只是对一个已存在类添加新内容的简单方法。在这里只是用来切分类的定义（jupyter notebook内教学使用，无特殊含义）。_

In [84]:
class BSBIIndex(BSBIIndex):
    def parse_block(self, block_dir_relative):
        """Parses a tokenized text file into termID-docID pairs

        Parameters
        ----------
        block_dir_relative : str
            Relative Path to the directory that contains the files for the block

        Returns
        -------
        List[Tuple[Int, Int]]
            Returns all the td_pairs extracted from the block

        Should use self.term_id_map and self.doc_id_map to get termIDs and docIDs.
        These persist across calls to parse_block
        """
        ### Begin your code
        #TODO 可能出现的问题,  td_pairs sorted 之后是否
        # 在相同term_id 下, 关于 term_id 升序, 在inverted_write 部分有说.
        # 感觉按这里的获取td_pairs 的方式 ,是有这样的性质
        block_path = os.path.join(self.data_dir, block_dir_relative)
        td_pairs = []
        for filename in sorted(os.listdir(block_path)):
            #BUG 到布尔检索那里才知道 要存路径。。。不过想想也是，应该存
            doc_id = self.doc_id_map[os.path.join(block_dir_relative,filename)]
            filepath = os.path.join(block_path, filename)
            unique_term_id = set()
            with open(filepath, 'r', encoding='utf-8') as f:
                words = f.read().split()
                for word in words:
                    term_id = self.term_id_map[word]
                    # not in 一个列表会是 O(n)的,
                    # 所以我之前这样去重，复杂度至少O(n^2)
                    # if (term_id, doc_id) not in td_pairs: #TODO 似乎不需要存词频，所以要去重
                    #     td_pairs.append((term_id, doc_id))
                    # 由于是一个个文件处理的，所以doc_id 是一样的
                    unique_term_id.add(term_id)
            # 转换然后给td_pairs 
            td_pairs += [(key, doc_id) for key in unique_term_id]
        return  td_pairs
        ### End your code

观察函数在测试数据上是否正常运行 (2%)

In [85]:
data_dir = "toy-data"
output_dir = "output_dir"
# actual_data_path = os.path.abspath(data_dir)
# print(f"实际路径 {actual_data_path}") 

with open("toy-data/0/fine.txt", "r") as f:
    print(f.read())
    # f.seek(0)
    # print(f.read())
with open("toy-data/0/hello.txt", "r") as f:
    print(f.read())
    
    
testBSBI_parse_block = BSBIIndex(data_dir, output_dir)
print(testBSBI_parse_block.parse_block("0")) # 有标点没关系。。实际用的文档是全部以空格隔开的
# print(f"有什么呢：\n{testBSBI_parse_block.term_id_map.id_to_str}")
print(testBSBI_parse_block.doc_id_map.str_to_id)
print(testBSBI_parse_block.term_id_map.str_to_id)

i'm fine , thank you

hi hi
how are you ?

[(0, 0), (1, 0), (2, 0), (3, 0), (4, 0), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1)]
{'0\\fine.txt': 0, '0\\hello.txt': 1}
{"i'm": 0, 'fine': 1, ',': 2, 'thank': 3, 'you': 4, 'hi': 5, 'how': 6, 'are': 7, '?': 8}


In [86]:
toy_dir = "toy-data"
current_dir = os.getcwd()
print("当前工作目录:", current_dir)
print(os.path.join(toy_dir, "0"))

当前工作目录: d:\1Learningoutput\Year2_Part2\Information_Retrieval\hw1
toy-data\0


In [87]:
BSBI_instance = BSBIIndex(data_dir=toy_dir, output_dir="tmp/", index_name="toy")
BSBI_instance.parse_block("0")

[(0, 0),
 (1, 0),
 (2, 0),
 (3, 0),
 (4, 0),
 (4, 1),
 (5, 1),
 (6, 1),
 (7, 1),
 (8, 1)]

写一些测试样例来确保`parse_block`方法正常运行（如：相同单词出现时是相同ID） (3%)

In [88]:
### Begin your code
#TODO 累的时候写，似乎我得弄个文件夹或者文件来存吧？毕竟只能从文件里读欸
### End your code

### 倒排表 (10%)

> The block is then inverted and written to disk. Inversion involves two steps. First, we sort the termID-docID pairs. Next, we collect all termID-docID pairs with the same termID into a postings list, where a posting is simply a docID. The result, an inverted index for the block we have just read, is then written to disk.

在这一部分我们添加函数`invert_write`来实现由termID-docID对构建倒排表。 

但是，我们首先需要实现类`InvertedIndexWriter`。和列表类似，该类提供了append函数，但是倒排表不会存储在内存中而是直接写入到磁盘里。 (3%)

In [89]:
class InvertedIndexWriter(InvertedIndex):
    """"""

    def __enter__(self):
        self.index_file = open(self.index_file_path, "wb+")
        return self

    def append(self, term, postings_list):
        """Appends the term and postings_list to end of the index file.

        This function does three things,
        1. Encodes the postings_list using self.postings_encoding
        2. Stores metadata in the form of self.terms and self.postings_dict
           Note that self.postings_dict maps termID to a 3 tuple of
           (start_position_in_index_file,
           number_of_postings_in_list,
           length_in_bytes_of_postings_list)
        3. Appends the bytestream to the index file on disk

        Hint: You might find it helpful to read the Python I/O docs
        (https://docs.python.org/3/tutorial/inputoutput.html) for
        information about appending to the end of a file.

        Parameters
        ----------
        term:
            term or termID is the unique identifier for the term
        postings_list: List[Int]
            List of docIDs where the term appears
        """
        ### Begin your code
        postings_list_encoded = self.postings_encoding.encode(postings_list)
        num_of_postings = len(postings_list)
        len_in_bytes = len(postings_list_encoded)
        #TODO 如果给的是term str 而不是ID int 该怎么办？
        self.terms.append(term)
        if not self.postings_dict:
            self.postings_dict[term] = (0, num_of_postings, len_in_bytes)
        else:
            last_values = next(reversed(self.postings_dict.values())) 
            start_pos = last_values[0] + last_values[2]
            self.postings_dict[term] = (start_pos, num_of_postings, len_in_bytes)
        self.index_file.write(postings_list_encoded)
        ### End your code

In [90]:
# for my test
with InvertedIndexWriter("test", directory="tmp/") as index:
    index.append(1, [2, 3, 4])
    index.append(2, [3, 4, 5])
    print(index.postings_dict)
    

{1: (0, 3, 12), 2: (12, 3, 12)}


尽管还没有实现读取索引的类，我们还是可以用以下测试代码检测我们的实现。 (2%)

In [91]:
with InvertedIndexWriter("test", directory="tmp/") as index:
    index.append(1, [2, 3, 4])
    index.append(2, [3, 4, 5])
    index.index_file.seek(0)
    assert index.terms == [1, 2], "terms sequence incorrect"
    assert index.postings_dict == {
        1: (0, 3, len(UncompressedPostings.encode([2, 3, 4]))),
        2: (
            len(UncompressedPostings.encode([2, 3, 4])),
            3,
            len(UncompressedPostings.encode([3, 4, 5])),
        ),
    }, "postings_dict incorrect"
    assert UncompressedPostings.decode(index.index_file.read()) == [
        2,
        3,
        4,
        3,
        4,
        5,
    ], "postings on disk incorrect"

现在我们实现 `invert_write`，它将解析得到的td_pairs转换成倒排表，并使用`InvertedIndexWriter` 类将其写入磁盘。 (3%)

In [92]:
class BSBIIndex(BSBIIndex):
    def invert_write(self, td_pairs, index):
        """Inverts td_pairs into postings_lists and writes them to the given index

        Parameters
        ----------
        td_pairs: List[Tuple[Int, Int]]
            List of termID-docID pairs
        index: InvertedIndexWriter
            Inverted index on disk corresponding to the block
        """
        ### Begin your code
        #TODO 如果没有元素。。。。后面的td_pairs[0][0]会有问题吧
        if not td_pairs:
            return
        #TODO 或许不该叫TODO， td_pairs 排序后， 每个词项对应的文档被放在一起了
        # 似乎对于每个词项id， 文档id 是升序的: 
        # 原来parse的时候,从列表首到尾,是按doc_id 升序的 
        # 然后sorted 说是稳定排序,也就是说由于根据term_id 排序,
        # 对于同一个 term_id, 原来在右边(doc_id大), 现在还在右边.
        td_pairs = sorted(td_pairs, key=lambda pair: pair[0])
        #TODO 也许不用再创建一个列表 
        # td_pairs.sort(key = lambda pair: pair[0])
        cur_term = td_pairs[0][0] 
        cur_postings_list = []
        for pair in td_pairs:
            if pair[0] != cur_term:
                index.append(cur_term, cur_postings_list)
                cur_term = pair[0]
                cur_postings_list = []
            cur_postings_list.append(pair[1])
        index.append(cur_term, cur_postings_list)
        ### End your code

我们可以在测试数据上读取一个块并观察倒排索引中包含的内容。
仿照`InvertedIndexWriter`部分写一些测试样例。 (2%)

In [93]:
### Begin your code
#TODO 待完善与检查
# 设计好多 类， 不方便测试 啊
data_dir = "toy-data"
output_dir = "output_dir"
test_invert_write = BSBIIndex(data_dir, output_dir)
index_name = "test_invert_write"
with InvertedIndexWriter(index_name, directory="tmp/") as index:
    td_pairs = [    
        [1, 2], [4, 2], [2, 3], [1, 3], [1, 4], 
    ]
    test_invert_write.invert_write(td_pairs,index)
    assert index.terms == [1,2,4]
    print(sorted(td_pairs, key=lambda pair: pair[0]))
    print(index.terms)
    print(index.postings_dict)
    
with open(f"tmp/{index_name}.index", 'rb') as f:
    content = f.read()
    content = UncompressedPostings.decode(content)
    print(content)


# 这是用 pickle 存的，直接打开来看没意义
# with open(f"tmp/{index_name}.dict", 'rb') as f:
#     content = f.read()
#     content = UncompressedPostings.decode(content)
#     print(content)

# with InvertedIndex(index_name, directory="tmp/") as index:
#     print(index.terms)
#     print(index.postings_dict)

# test_invert_write2 = BSBIIndex(data_dir, output_dir)


### End your code

[[1, 2], [1, 3], [1, 4], [2, 3], [4, 2]]
[1, 2, 4]
{1: (0, 3, 12), 2: (12, 1, 4), 4: (16, 1, 4)}
[2, 3, 4, 3, 2]


### 合并 (10%)
> The algorithm simultaneously merges the ten blocks into one large merged index. To do the merging, we open all block files simultaneously, and maintain small read buffers for the ten blocks we are reading and a write buffer for the final merged index we are writing. 

Python中的迭代模型非常自然地符合我们维护一个小的读缓存的要求。我们可以迭代地从磁盘上每次读取文件的一个倒排列表。我们通过构建`InvertedIndex`的子类`InvertedIndexIterator`来完成这个迭代任务。 (3%)

In [94]:
class InvertedIndexIterator(InvertedIndex):
    """"""

    def __enter__(self):
        """Adds an initialization_hook to the __enter__ function of super class"""
        super().__enter__()
        self._initialization_hook()
        return self

    def _initialization_hook(self):
        """Use this function to initialize the iterator"""
        ### Begin your code
        #TODO 说是postings_dict 已经有序了, 我先试着不适用terms
        # next(self.term_iter)
        self.postings_dict_iter = self.postings_dict.items().__iter__()
        self.index_file.seek(0)
        ### End your code

    def __iter__(self):
        return self

    def __next__(self):
        """Returns the next (term, postings_list) pair in the index.

        Note: This function should only read a small amount of data from the
        index file. In particular, you should not try to maintain the full
        index file in memory.
        """
        ### Begin your code
        #TODO 也许不该用todo ， 注意返回的是 ID 而不是str
        nex_term, term_metadata = next(self.postings_dict_iter)
        #TODO 也许这个seek 可以去掉？每次read之后指针自己会变
        self.index_file.seek(term_metadata[0])
        postings_list_bytes = self.index_file.read(term_metadata[2])
        
        postings_list = self.postings_encoding.decode(postings_list_bytes)
        return (nex_term, postings_list)
        ### End your code

    def delete_from_disk(self):
        """Marks the index for deletion upon exit. Useful for temporary indices"""
        self.delete_upon_exit = True

    def __exit__(self, exception_type, exception_value, traceback):
        """Delete the index file upon exiting the context along with the
        functions of the super class __exit__ function"""
        self.index_file.close()
        if hasattr(self, "delete_upon_exit") and self.delete_upon_exit:
            os.remove(self.index_file_path)
            os.remove(self.metadata_file_path)
        else:
            with open(self.metadata_file_path, "wb") as f:
                pkl.dump([self.postings_dict, self.terms], f)

为了测试以上代码，我们先用`InvertedIndexWriter` 创建索引，然后再迭代遍历。写一些小的测试样例观察它是否正常运行。至少你得写一个测试，手工构建一个小的索引，用`InvertedIndexWriter`将他们写入磁盘，然后用`InvertedIndexIterator`迭代遍历倒排索引。 (2%)

In [95]:
### Begin your code
#TODO 待完善与检查
data_dir = "toy-data"
output_dir = "output_dir"
test_index_iter = BSBIIndex(data_dir, output_dir)
index_name = "test_index_iter"
with InvertedIndexWriter(index_name, directory="tmp/") as index:
    td_pairs = [    
        [1, 2], [4, 2], [2, 3], [1, 3], [1, 4], [4,5],[2,5], [2,10]
    ]
    test_index_iter.invert_write(td_pairs,index)
    assert index.terms == [1,2,4]
    print(sorted(td_pairs, key=lambda pair: pair[0]))
    print(index.terms)
    print(index.postings_dict)
    
with InvertedIndexIterator(index_name, directory="tmp/") as index:
    # all_postings = index.postings_encoding.decode(index.index_file.read())
    # print(all_postings)
    #TODO 似乎不应该叫TODO。在这里才找出invert_write 里的一个写错的地方
    # 说明每个函数写完之后，不要偷懒。。。应该写点测试，至少是print语句，
    # 验证写对了。
    assert next(index)== (1, [2,3,4]),"termid 1 incorrect"
    assert next(index) == (2, [3, 5, 10]), "termid 2 incorrect"
    assert next(index) == (4, [2, 5]), "termid 3 incorrect"
    try:
        next(index)
    except StopIteration:
        pass
    else: 
        assert False, "should not have more terms"
    


### End your code

[[1, 2], [1, 3], [1, 4], [2, 3], [2, 5], [2, 10], [4, 2], [4, 5]]
[1, 2, 4]
{1: (0, 3, 12), 2: (12, 3, 12), 4: (24, 2, 8)}


> During merging, in each iteration, we select the lowest termID that has not been processed yet using a priority queue or a similar data structure. All postings lists for this termID are read and merged, and the merged list is written back to disk. Each read buffer is refilled from its file when necessary.

我们将使用`InvertedIndexIterator`来完成读取的部分，用`InvertedIndexWriter`来将合并后的索引写入磁盘。

注意到我们之前一直使用`with` 语句来打开倒排索引文件，但是现在需要程序化地完成这项工作。可以看到我们在基类`BSBIIndex`的`index`函数中使用了`contextlib`([参考文档](https://docs.python.org/3/library/contextlib.html#contextlib.ExitStack))
你的任务是合并*打开的*`InvertedIndexIterator`对象（倒排列表），并且通过一个`InvertedIndexWriter`对象每次写入一个文档列表。

既然我们知道文档列表已经排过序了，那么我们可以在线性时间内对它们进行合并排序。事实上`heapq`([参考文档](https://docs.python.org/3.0/library/heapq.html)) 是Python中一个实现了堆排序算法的标准模板。另外它还包含一个实用的函数`heapq.merge`，可以将多个已排好序的输入（可迭代）合并成一个有序的输出并返回它的迭代器。它不仅可以用来合并倒排列表，也可以合并倒排索引词典。

为了让你快速上手`heapq.merge`函数，我们提供了一个简单的使用样例。给出两个以动物和树平均寿命排序的列表，我们希望合并它们。

In [96]:
import heapq

animal_lifespans = [
    ("Giraffe", 28),
    ("Rhinoceros", 40),
    ("Indian Elephant", 70),
    ("Golden Eagle", 80),
    ("Box turtle", 123),
]

tree_lifespans = [
    ("Gray Birch", 50),
    ("Black Willow", 70),
    ("Basswood", 100),
    ("Bald Cypress", 600),
]

lifespan_lists = [animal_lifespans, tree_lifespans]

for merged_item in heapq.merge(*lifespan_lists, key=lambda x: x[1]):
    print(merged_item)

('Giraffe', 28)
('Rhinoceros', 40)
('Gray Birch', 50)
('Indian Elephant', 70)
('Black Willow', 70)
('Golden Eagle', 80)
('Basswood', 100)
('Box turtle', 123)
('Bald Cypress', 600)


注意使用`*`将`lifespan_lists`解包作为参数，并且使用`lambda`函数来给出进行排序的key。如果你对它们不熟悉可以参考文档([unpacking lists](https://docs.python.org/3/tutorial/controlflow.html#unpacking-argument-lists), [lambda expressions](https://docs.python.org/3/tutorial/controlflow.html#lambda-expressions))。 (3%)

In [97]:
import heapq


class BSBIIndex(BSBIIndex):
    def merge(self, indices, merged_index):
        """Merges multiple inverted indices into a single index

        Parameters
        ----------
        indices: List[InvertedIndexIterator]
            A list of InvertedIndexIterator objects, each representing an
            iterable inverted index for a block
        merged_index: InvertedIndexWriter
            An instance of InvertedIndexWriter object into which each merged
            postings list is written out one at a time
        """
        ### Begin your code
        # 维护一个list用来存？
        # 然后每次把最小的词项。。。弄出来？ 直到所有弄完？
        # 好吧， heapq.merge就是干这个事情的
        cur_term = 0
        cur_postings = []
        for merged_item in heapq.merge(*indices): # 这里有term_id 吧？
            if merged_item[0] != cur_term:
                merged_index.append(cur_term, cur_postings)
                # 由于每个存到 termidmap 里的都是有term-doc pair的词， 编号是相邻的
                # 好吧，用 merged_item[0] 更保险
                #BUG FIX 写成+= 了，怪不得少了很多键
                cur_term = merged_item[0] # merged_item 没有了自然会停，不是无限循环
                cur_postings = []
            cur_postings += merged_item[1] # merged_item[1] 是一个 list 
        merged_index.append(cur_term, cur_postings) # 没东西了，也要存一下
        
        ### End your code

首先确保它在测试数据上正常运行

In [98]:
BSBI_instance = BSBIIndex(
    data_dir=toy_dir,
    output_dir="toy_output_dir",
)
BSBI_instance.index()

In [99]:
### my test
with InvertedIndexIterator("BSBI", directory="./toy_output_dir/") as index:
    print(index.postings_dict)
    print(index.terms)

{0: (0, 2, 8), 1: (8, 2, 8), 2: (16, 3, 12), 3: (28, 2, 8), 4: (36, 5, 20), 5: (56, 2, 8), 6: (64, 2, 8), 7: (72, 2, 8), 8: (80, 3, 12), 9: (92, 1, 4), 10: (96, 1, 4), 11: (100, 1, 4), 12: (104, 2, 8), 13: (112, 1, 4)}
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13]


接下来对整个数据集构建索引 (2%)

In [100]:
BSBI_instance = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir",
)
BSBI_instance.index()

如果你在合并阶段出现了错误，可以利用以下代码来debug。

In [101]:
BSBI_instance = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir",
)
BSBI_instance.intermediate_indices = ["index_" + str(i) for i in range(10)]
with InvertedIndexWriter(
    BSBI_instance.index_name,
    directory=BSBI_instance.output_dir,
    postings_encoding=BSBI_instance.postings_encoding,
) as merged_index:
    with contextlib.ExitStack() as stack:
        indices = [
            stack.enter_context(
                InvertedIndexIterator(
                    index_id,
                    directory=BSBI_instance.output_dir,
                    postings_encoding=BSBI_instance.postings_encoding,
                )
            )
            for index_id in BSBI_instance.intermediate_indices
        ]
        BSBI_instance.merge(indices, merged_index)

## 布尔联合检索 (10%)

我们将实现BSBIIndex中的`retrieve`函数，对于给定的包含由空格分隔tokens的字符串查询，返回包含查询中所有tokens的文档列表。但是我们并不能迭代遍历整个索引或者将整个索引加载到内存来寻找相应的terms（索引太大）。

首先我们要实现`InvertedIndex`的子类`InvertedIndexMapper`，它能够找到对应terms在索引文件中位置并取出它的倒排记录表。 (2%)

In [102]:
class InvertedIndexMapper(InvertedIndex):
    def __getitem__(self, key):
        return self._get_postings_list(key)

    def _get_postings_list(self, term):
        """Gets a postings list (of docIds) for `term`.

        This function should not iterate through the index file.
        I.e., it should only have to read the bytes from the index file
        corresponding to the postings list for the requested term.
        """
        ### Begin your code
        #TODO 这个term 应该是termid吧，因为map 在BSBI里面，InvertedIndex里用不了
        start_pos, _, len_in_bytes = self.postings_dict[term]
        self.index_file.seek(start_pos)
        postings_list_in_bytes = self.index_file.read(len_in_bytes)
        return self.postings_encoding.decode(postings_list_in_bytes)
        ### End your code

写一些测试样例检测`_get_postings_list`的实现 (1%)

In [103]:
### Begin your code
with InvertedIndexMapper("BSBI", directory="output_dir") as index:
    # print(index._get_postings_list(3))
    print(index.postings_dict)
### End your code

{0: (0, 849, 3396), 1: (3396, 429, 1716), 2: (5112, 7868, 31472), 3: (36584, 71202, 284808), 4: (321392, 56709, 226836), 5: (548228, 20874, 83496), 6: (631724, 85566, 342264), 7: (973988, 6208, 24832), 8: (998820, 79688, 318752), 9: (1317572, 565, 2260), 10: (1319832, 1637, 6548), 11: (1326380, 71951, 287804), 12: (1614184, 81770, 327080), 13: (1941264, 19460, 77840), 14: (2019104, 36750, 147000), 15: (2166104, 51551, 206204), 16: (2372308, 28944, 115776), 17: (2488084, 14844, 59376), 18: (2547460, 7258, 29032), 19: (2576492, 7158, 28632), 20: (2605124, 4895, 19580), 21: (2624704, 79116, 316464), 22: (2941168, 5555, 22220), 23: (2963388, 13632, 54528), 24: (3017916, 66675, 266700), 25: (3284616, 4245, 16980), 26: (3301596, 15655, 62620), 27: (3364216, 3931, 15724), 28: (3379940, 15389, 61556), 29: (3441496, 43901, 175604), 30: (3617100, 37843, 151372), 31: (3768472, 3718, 14872), 32: (3783344, 2595, 10380), 33: (3793724, 3630, 14520), 34: (3808244, 1202, 4808), 35: (3813052, 2598, 1039

现在我们获得了查询中terms对应的倒排记录表，接着需要求他们的交集。这部分与我们之前作业的merge方法类似，请实现`sorted_intersect`函数，遍历两个有序列表并在线性时间内合并。 (2%)

In [104]:
def sorted_intersect(list1, list2):
    """Intersects two (ascending) sorted lists and returns the sorted result

    Parameters
    ----------
    list1: List[Comparable]
    list2: List[Comparable]
        Sorted lists to be intersected

    Returns
    -------
    List[Comparable]
        Sorted intersection
    """
    ### Begin your code
    merged = heapq.merge(list1, list2)
    result = []
    prev = None
    for doc_id in merged:
        if prev == doc_id:
            result.append(doc_id)
        else:
            prev = doc_id
    return result
    # 写成求不重复的并集了
    # seen = set()
    # for doc_id in merged:
    #     if doc_id not in seen:
    #         seen.add(doc_id)
    #     else:
    #         result.append(doc_id)
    # return result
    ### End your code

简单的测试样例 (1%)

In [105]:
### Begin your code
#TODO 尝试一下directory="./toy_output_dir/" 
# 与 directory="toy_output_dir" 有没有区别
# 似乎就是看看 os.path.join 有没有那么多判断逻辑？？
with InvertedIndexMapper("BSBI",directory="output_dir") as index:
    list1 = index._get_postings_list(0)
    list2 = index._get_postings_list(2)
    # print(list1)
    # print(list2)
    simple_merge_result = list(sorted(set(list1) & set(list2)))
    # print(simple_merge_result)
    # print(sorted_intersect(list1,list2))
    assert simple_merge_result == sorted_intersect(list1,list2),"not equal"
    
### End your code

现在可以利用`sorted_intersect` 和 `InvertedIndexMapper`来实现`retrieve`函数。 (3%)

In [106]:
# %%tee submission/retrieve.py
#TODO 上面这个是什么？
class BSBIIndex(BSBIIndex):
    def retrieve(self, query:str):
        """Retrieves the documents corresponding to the conjunctive query
        
        Parameters
        ----------
        query: str
            Space separated list of query tokens
            
        Result
        ------
        List[str]
            Sorted list of documents which contains each of the query tokens. 
            Should be empty if no documents are found.
        
        Should NOT throw errors for terms not in corpus
        """
        if len(self.term_id_map) == 0 or len(self.doc_id_map) == 0:
            self.load()

        ### Begin your code
        with InvertedIndexMapper(self.index_name, self.postings_encoding, directory=self.output_dir) as index:
            # print(query.split())
            # print(list(index.postings_dict.items())[:10])
            words_id_list = [self.term_id_map[word] for word in query.split()]
            # print(words_id_list)
            retrieve_lists = [index[word_id] for word_id in words_id_list]
            retrieve_lists.sort(key=lambda x:len(x))
            # print(retrieve_lists)
            result = retrieve_lists[0] # 从最短的开始。。。 不过这样真的会快吗，我前面用了一个排序.
            for i in range(1,len(retrieve_lists)):
                result = sorted_intersect(result, retrieve_lists[i])
                if has_duplicates_sorted(result):
                    print(f"{i} 个位置，WRONG")
            if has_duplicates_sorted(result):
                print("有问题")
        result = [self.doc_id_map[doc_id] for doc_id in result]
        if has_duplicates_sorted(result):
            print("返回之前出事了")
        return result
        ### End your code

# for test
def has_duplicates_sorted(lst):
    for i in range(1, len(lst)):  # 从第二个元素开始
        if lst[i] == lst[i - 1]:  # 只需要比较相邻元素
            return True
    return False


通过一个简单的查询来测试索引在真实数据集上是否正常工作。

In [107]:
BSBI_instance = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir",
)
BSBI_instance.retrieve("boolean retrieval")
# BSBI_instance.retrieve("hello world")

['1\\cs276.stanford.edu_',
 '1\\cs276a.stanford.edu_',
 '3\\infolab.stanford.edu_TR_CS-TN-95-21.html',
 '4\\nlp.stanford.edu_IR-book_',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_an-appraisal-of-probabilistic-models-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_bayesian-network-approaches-to-ir-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_boolean-retrieval-2.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_computing-scores-in-a-complete-search-system-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_dictionaries-and-tolerant-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_efficient-scoring-and-ranking-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_inexact-top-k-document-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_probabilistic-information-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_putting-it-all-together-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_references-and-furth

你也可以通过读取文件来测试其中的页面是否真的包含了查询的terms

In [108]:
with open("pa1-data/1/cs276.stanford.edu_", "r") as f:
    print(f.read())

cs276 information retrieval and web search cs 276 ling 286 information retrieval and web search spring 2011 pandu nayak and prabhakar raghavan lecture 3 units tu th 4 15 5 30 gates b03 tas sonali aggarwal ivan cui valentin spitkovsky and sandeep sripada staff e mail cs276 spr1011 staff lists stanford edu lectures are also available online and on television through scpd sitn course description basic and advanced techniques for text based information systems efficient text indexing boolean and vector space retrieval models evaluation and interface issues web search including crawling link based algorithms and web metadata text web clustering classification text mining syllabus additional information staff contact information piazzza we strongly recommend students to post questions to the course page on www piazzza com instead of sending emails this forum enables students to discuss the questions they encounter in lectures or assignments here is a quick introduction video email if you hav

测试dev queries（提前构建好的查询与结果）是否正确 (1%)

In [109]:
#TODO 到这里才知道 doc_id_map 要把 块路径也存进去作为 str
for i in range(1, 9):
    with open("dev_queries/query." + str(i)) as q:
        query = q.read()
        my_results = [os.path.normpath(path) for path in BSBI_instance.retrieve(query)]
        with open("./debug_retrieve/" + str(i) + ".out", "w") as debug:
            for item in my_results:
                debug.write(item + "\n")
        with open("dev_output/" + str(i) + ".out") as o:
            reference_results = [os.path.normpath(x.strip()) for x in o.readlines()]
            # my_results.sort()
            # reference_results.sort()
            # if my_results != reference_results:
            #     print(my_results)
            #     print(reference_results)
            #     print(i)
            #     print(query)
            assert my_results == reference_results, (
                "Results DO NOT match for query: " + query.strip()
            )
        print("Results match for query:", query.strip())

Results match for query: we are
Results match for query: stanford class
Results match for query: stanford students
Results match for query: very cool
Results match for query: the
Results match for query: a
Results match for query: the the
Results match for query: stanford computer science


如果出现了错误，可以通过以下代码比较输出与正确结果的差异

In [110]:
set(my_results) - set(reference_results)

set()

In [111]:
set(reference_results) - set(my_results)

set()

确保你构建自己的查询来测试所有可能的边界情况，例如数据集中没有出现的terms，或者拖慢合并的频繁出现的terms。

# 索引压缩  (30%)

在这部分，你将使用可变长字节编码对索引进行压缩。（gap-encoding可选，对gap进行编码）

下面几个Python运算符可能对你有帮助

In [112]:
# Remainder (modulo) operator %

print("10 % 2 = ", 10 % 2)
print("10 % 3 = ", 10 % 3)

# Integer division in Python 3 is done by using two slash signs

print("10 / 3 = ", 10 / 3)
print("10 // 3 = ", 10 // 3)

10 % 2 =  0
10 % 3 =  1
10 / 3 =  3.3333333333333335
10 // 3 =  3


完成下面的`CompressedPostings`类，我们将用它来替换`UncompressedPostings`。关于如何使用gap-encoding和可变长字节编码，你可以参考老师课件或者[Chapter 5](https://nlp.stanford.edu/IR-book/pdf/05comp.pdf)。 (18%)

In [113]:
class CompressedPostings:
    # If you need any extra helper methods you can add them here
    ### Begin your code
    @staticmethod
    def encode_number(num):
        out = array.array("B")
        if num == 0:
            out.insert(0, int("0000_0000",base=2))
            return out
        is_end_byte = True
        while num > 0:
            to_encode = num % 128 # 2^7 = 128
            num = num // 128
            to_encode = f"{to_encode:07b}"
            if is_end_byte:
                out.insert(0, int(f"0{to_encode}",base=2)) # 需要7位对齐
                is_end_byte = False
            else:
                out.insert(0, int(f"1{to_encode}",base=2)) 
        return out
    ### End your code

    @staticmethod
    def encode(postings_list):
        """Encodes `postings_list` using gap encoding with variable byte
        encoding for each gap

        Parameters
        ----------
        postings_list: List[int]
            The postings list to be encoded

        Returns
        -------
        bytes:
            Bytes reprsentation of the compressed postings list
            (as produced by `array.tobytes` function)
        """
        ### Begin your code
        # 先变成 gap 
        gap_list = [postings_list[0]] + \
                    [postings_list[i+1] - postings_list[i] for i in range(0, len(postings_list)-1) ]
        
        # 再编码
        result = array.array("B")
        for item in gap_list:
            encoded_item = CompressedPostings.encode_number(item)
            result += encoded_item
        return result.tobytes()
        ### End your code

    @staticmethod
    def decode(encoded_postings_list):
        """Decodes a byte representation of compressed postings list

        Parameters
        ----------
        encoded_postings_list: bytes
            Bytes representation as produced by `CompressedPostings.encode`

        Returns
        -------
        List[int]
            Decoded postings list (each posting is a docIds)
        """
        ### Begin your code
        result = []
        array_restore = array.array("B")
        array_restore.frombytes(encoded_postings_list)
        cur_decoded_num = 0
        for item in array_restore:
            value = item & 0b0111_1111
            cur_decoded_num = (cur_decoded_num << 7) | value # 并上去
            if item >> 7 == 0:
                # 最后一个字节一定是0 开头的
                result.append(cur_decoded_num + (result[-1] if len(result)>0 else 0)) # if else 三元运算符前面表达式得加括号，否则会尽可能延伸
                cur_decoded_num = 0
        return result
        ### End your code

首先，如果你实现了额外的辅助函数，写一些测试样例

In [114]:
### Begin your code
test_array = array.array("B")
test_array.append(int(f"0{4:07b}",base=2))
assert CompressedPostings.encode_number(4) == test_array

test_array2 = array.array("B")
# 11280 = "1011000_0010000"
part1 = "1011000"
part2 = "0010000"
test_array2.append(int(f"1{part1}", base=2))
test_array2.append(int(f"0{part2}", base=2))

assert CompressedPostings.encode_number(11280) == test_array2

# test encode
CompressedPostings.encode([2,3,4,5, 128])
### End your code

b'\x02\x01\x01\x01{'

我们实现了一个简单的函数来测试你编码的列表是否被正确解码

In [115]:
def test_encode_decode(l):
    e = CompressedPostings.encode(l)
    d = CompressedPostings.decode(e)
    assert d == l
    print(l, e)
    print(d)
test_encode_decode([2,3,4,235,2335,3546346])
test_encode_decode([0,23,333, 434,42342,223232])

[2, 3, 4, 235, 2335, 3546346] b'\x02\x01\x01\x81g\x904\x81\xd8\xa7K'
[2, 3, 4, 235, 2335, 3546346]
[0, 23, 333, 434, 42342, 223232] b'\x00\x17\x826e\x82\xc74\x8b\x85\x1a'
[0, 23, 333, 434, 42342, 223232]


写一些测试样例来确保文档列表的压缩和解压正常运行 (2%)

In [116]:
### Begin your code
#TODO
### End your code

现在让我们创建一个新的输出文件夹并使用`CompressedPostings`来构建压缩索引

In [117]:
try:
    os.mkdir("output_dir_compressed")
except FileExistsError:
    pass

In [ ]:
BSBI_instance_compressed = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir_compressed",
    postings_encoding=CompressedPostings,
)
BSBI_instance_compressed.index()

In [119]:
BSBI_instance_compressed = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir_compressed",
    postings_encoding=CompressedPostings,
)
BSBI_instance_compressed.retrieve("boolean retrieval")

['1\\cs276.stanford.edu_',
 '1\\cs276a.stanford.edu_',
 '3\\infolab.stanford.edu_TR_CS-TN-95-21.html',
 '4\\nlp.stanford.edu_IR-book_',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_an-appraisal-of-probabilistic-models-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_bayesian-network-approaches-to-ir-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_boolean-retrieval-2.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_computing-scores-in-a-complete-search-system-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_dictionaries-and-tolerant-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_efficient-scoring-and-ranking-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_inexact-top-k-document-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_probabilistic-information-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_putting-it-all-together-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_references-and-furth

像之前一样，用已构造好的查询语句来测试是否正常运行 (5%)

In [120]:
for i in range(1, 9):
    with open("dev_queries/query." + str(i)) as q:
        query = q.read()
        my_results = [
            os.path.normpath(path) for path in BSBI_instance_compressed.retrieve(query)
        ]
        with open("dev_output/" + str(i) + ".out") as o:
            reference_results = [os.path.normpath(x.strip()) for x in o.readlines()]
            assert my_results == reference_results, (
                "Results DO NOT match for query: " + query.strip()
            )
        print("Results match for query:", query.strip())

Results match for query: we are
Results match for query: stanford class
Results match for query: stanford students
Results match for query: very cool
Results match for query: the
Results match for query: a
Results match for query: the the
Results match for query: stanford computer science


请追加压缩前后的文件大小截图 (5%)

# 额外的编码方式 (10%)

通过补充`ECCompressedPostings`的`encode` 和 `decode`方法来实现一种额外的索引压缩方式。在我们课上学的就是**gamma-encoding** 。另外如果大家感兴趣的话也可以了解**Delta Encoding** ，[ALGORITHM SIMPLE-9](https://github.com/manning/CompressionAlgorithms#simple-9) 等。

你应该以多字节（而不是bits）来存储倒排记录表，因为索引的长度和位置都存的是字节信息。 (4%)

In [121]:
class ECCompressedPostings:
    # If you need any extra helper methods you can add them here
    ### Begin your code
    @staticmethod
    def gamma_encode(n):
        """encode a single number
        
        Parameters
        ----------
        n: int
            number
        
        Returns
        -------
        str:
            string of gamma encoded of n
        
        """
        if n <= 0:
            raise ValueError("gamma_encode nees positive number")
        binary = bin(n)[3:]
        unary = "1"*len(binary) + "0"
        return unary + binary
    
    @staticmethod
    def gamma_decode(bit_seq, suffix_len):
        """encode a single number
        
        Parameters
        ----------
        bit_seq: BitArray
            a BitArray of gamma encoded number
        
        suffix_len: int
            len of original number in binary representation
            excluding the leftest 1 
        
        
        Returns
        -------
        int:
            original number
        
        """
        if len(bit_seq) == 0:
            return 1
        return int("1" + bit_seq[suffix_len+1:].bin, base=2 )
        
        
    
    @staticmethod
    def list_to_gap_list(lst):
        """Transform a list to a gap list
        Parameters
        ---------
        lst:List[int]
            list to be transformed
            
        Returns
        -------
        List[int]
            a gap list
        
        """
        gap_list = [lst[0]] + \
                    [lst[i+1] - lst[i] for i in range(0, len(lst)-1) ]
        return gap_list 
    
    @staticmethod
    def gap_list_to_list(lst):
        """Transform a gap list to a original list
        Parameters
        ---------
        lst:List[int]
            a gap list
            
        Returns
        -------
        List[int]
            lst's original list
        
        """
        orig_lst = lst[:]
        for i in range(1, len(orig_lst)):
            orig_lst[i] += orig_lst[i-1]
        return orig_lst
    ### End your code

    @staticmethod
    def encode(postings_list):
        """Encodes `postings_list`

        Parameters
        ----------
        postings_list: List[int]
            The postings list to be encoded

        Returns
        -------
        bytes:
            Bytes reprsentation of the compressed postings list
        """
        ### Begin your code
        # 先变成 gap 
        gap_lst = ECCompressedPostings.list_to_gap_list(postings_list)
        
        # 对第一个单独+1， 因为可能doc_id == 0
        gap_lst[0] += 1
        bit_seq = BitArray()
        for num in gap_lst:
            bit_seq.append("0b" + ECCompressedPostings.gamma_encode(num))

        not_aligned_len = len(bit_seq) % 8
        # 使用1 来填充， 若用0， 会被误解码成 数字 1
        if not_aligned_len != 0:
            # print("not aligned")
            bit_seq.append("0b" + "1"*(8- not_aligned_len))

        # 前面手动补1 了，这里不会为了对齐而补零
        bytes_result = bit_seq.tobytes()
        return bytes_result
        ### End your code

    @staticmethod
    def decode(encoded_postings_list):
        """Decodes a byte representation of compressed postings list

        Parameters
        ----------
        encoded_postings_list: bytes
            Bytes representation as produced by `CompressedPostings.encode`

        Returns
        -------
        List[int]
            Decoded postings list (each posting is a docId)
        """
        ### Begin your code
        #TODO 似乎都没想如果传进来空的怎么办...很多函数，包括这个
        bit_seq = BitArray(encoded_postings_list)
        gap_lst = [] # gap_lst 的第一个并非距离；或者说与0的距离
        cur_gap = 0
        i = 0
        is_rest_padding = False
        while i<len(bit_seq):
            suffix_len = 0
            # 由于我最后用 1 padding， 所以需要跳出循环
            while bit_seq[i]:
                # 非padding 不会到最后一个还是 unary code 的
                if i == len(bit_seq) - 1: 
                    is_rest_padding = True
                    break
                suffix_len += 1
                i+=1
            if is_rest_padding:
                break
            cur_gap = ECCompressedPostings.gamma_decode(bit_seq[i-suffix_len:i+suffix_len+1], suffix_len)
            i += suffix_len + 1  # 跳过后缀部分
            suffix_len = 0
            gap_lst.append(cur_gap)
        # 是在 gap_list 与 list 转换之后 +1 的，所以这里转回去也要 -1 
        gap_lst[0] -=1
        return ECCompressedPostings.gap_list_to_list(gap_lst)
        
        ### End your code

同上，写一些测试样例来确保代码正常运行 (3%)

In [122]:
### Begin your code
# test helper func
assert ECCompressedPostings.gamma_encode(3) == "101"
assert ECCompressedPostings.gamma_encode(135) == \
    "1"*7+"0"+"0000111"
    # str.replace("1"*7 + "0" + "000_0111","_","")
    
assert ECCompressedPostings.list_to_gap_list([3,6,8,999]) == \
    [3,3,2,991]
assert ECCompressedPostings.gap_list_to_list([3,3,2,991]) == \
    [3,6,8,999]
    
    
def test_encode_decode(l):
    e = ECCompressedPostings.encode(l)
    d = ECCompressedPostings.decode(e)
    assert d == l
    print(l)
    print(e)
    print(d)
test_encode_decode([0,1,2,3])
test_encode_decode([234,262462,2352333, 732979479])
test_encode_decode([2,334,5235,23523,234232])
    
# test encode and decode
#TODO




### End your code

[0, 1, 2, 3]
b'\x0f'
[0, 1, 2, 3]
[234, 262462, 2352333, 732979479]
b'\xfe\xd7\xff\xff\x80\x05O\xff\xff\x7f\x1c\x7f\xff\xff\xff\xcb\x8c|J'
[234, 262462, 2352333, 732979479]
[2, 334, 5235, 23523, 234232]
b'\xbf\xe4\xcf\xff\x19/\xff\xe1\xdc?\xff\xe9\xb8\xaf'
[2, 334, 5235, 23523, 234232]


In [124]:
try:
    os.mkdir("output_dir_ECCcompressed")
except FileExistsError:
    pass

In [126]:
BSBI_instance_ECCcompressed = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir_ECCcompressed",
    postings_encoding=ECCompressedPostings,
)
BSBI_instance_ECCcompressed.index()

In [127]:
# try to compress
BSBI_instance_ECCcompressed = BSBIIndex(
    data_dir="pa1-data",
    output_dir="output_dir_ECCcompressed",
    postings_encoding=ECCompressedPostings,
)
BSBI_instance_ECCcompressed.retrieve("boolean retrieval")


['1\\cs276.stanford.edu_',
 '1\\cs276a.stanford.edu_',
 '3\\infolab.stanford.edu_TR_CS-TN-95-21.html',
 '4\\nlp.stanford.edu_IR-book_',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_an-appraisal-of-probabilistic-models-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_bayesian-network-approaches-to-ir-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_boolean-retrieval-2.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_computing-scores-in-a-complete-search-system-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_dictionaries-and-tolerant-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_efficient-scoring-and-ranking-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_inexact-top-k-document-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_probabilistic-information-retrieval-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_putting-it-all-together-1.html',
 '4\\nlp.stanford.edu_IR-book_html_htmledition_references-and-furth

In [128]:
for i in range(1, 9):
    with open("dev_queries/query." + str(i)) as q:
        query = q.read()
        my_results = [
            os.path.normpath(path) for path in BSBI_instance_ECCcompressed.retrieve(query)
        ]
        with open("dev_output/" + str(i) + ".out") as o:
            reference_results = [os.path.normpath(x.strip()) for x in o.readlines()]
            assert my_results == reference_results, (
                "Results DO NOT match for query: " + query.strip()
            )
        print("Results match for query:", query.strip())

Results match for query: we are
Results match for query: stanford class
Results match for query: stanford students
Results match for query: very cool
Results match for query: the
Results match for query: a
Results match for query: the the
Results match for query: stanford computer science


请追加压缩前后的文件大小截图 (3%)

# 作业提交

本次作业用时约3周，截止日期为2024.03.26。请大家在截止日期前将代码、实验报告（可单独撰写，也可整合在jupyter notebook中）一起提交到ir24fall@163.com，邮件和文件命名方式均为`学号_姓名_hw1`，如`1811412_戚晓睿_hw1.ipynb`